In [1]:
from IPython import display
import math
from pprint import pprint
import pandas as pd
import nltk
import numpy as np
import nltk

In [2]:
# import matplotlib.pyplot as plt
# import seaborn as sns
# sns.set(style='darkgrid', context='talk', palette='Dark2')

In [3]:
# ['gameplay', 'price', 'cheat', 'optimization', 'graphic']

In [4]:
from ast import literal_eval
df_test = pd.read_csv('feature_extraction_pubg_new.csv',sep = '\t')
# if need to transform pandas series back to original type
position_list = [literal_eval(dic) for dic in df_test['feature_positions']]
print(position_list[0])

{1: 2}


In [5]:
df_test.loc[9999,]['review']

'I have already tried to refund this game, but I am past both dead lines, so it\'s kind of just sitting in my game library with no real purpose. I do not like how this game feel when you play it. The graphics, landscape, and driving might be fine, but the shooting, and chances of dying of some stupid cause makes me hate this game a lot more than I thought I would. I also do not enjoy that this out of many battle royale type survival series, have to have battle or "season pass". I have already spent money on your game, don\'t put options for better cosmetics and expect me to buy them.'

In [6]:
r = df_test.loc[9999,]['review']
words = nltk.word_tokenize(r)
words[9]

'but'

In [7]:
df_test.loc[9999,]

review               I have already tried to refund this game, but ...
feature_positions                {47: 6, 67: 2, 93: 0, 102: 0, 113: 3}
Name: 9999, dtype: object

In [8]:
W = 5
position_list = [literal_eval(dic) for dic in df_test['feature_positions']]
reviews = df_test['review'].tolist()
review_windows = dict()

In [9]:
for review_idx in range(len(reviews)):
    if review_idx % 10000 == 0:
        print(review_idx)
    review = reviews[review_idx]
    tokens = nltk.word_tokenize(review)
    feature_pos = position_list[review_idx]
    sentiment_windows = []
    for token_index, category in feature_pos.items():
        if token_index <= W:
            candidate = " ".join(tokens[:token_index+W+1])
        elif token_index+W > len(tokens):
            candidate = " ".join(tokens[token_index-W:])
        else:
            candidate = " ".join(tokens[token_index-W:token_index+W+1])
        sentiment_windows.append((candidate,category))
    review_windows[review_idx] = sentiment_windows

0
10000
20000
30000
40000
50000
60000
70000
80000
90000
100000
110000
120000


In [ ]:
# n_reviews = len(df_test)
# for i in range(n_reviews):
#     review = df_test.loc[i,]['review']
#     feature_positions = df_test.loc[i,]['feature_positions']

## Sentiment Analysis Model 1

In [10]:
from nltk.sentiment.vader import SentimentIntensityAnalyzer as SIA

In [11]:
nltk.download('vader_lexicon')

[nltk_data] Downloading package vader_lexicon to
[nltk_data]     /Users/jaclyn/nltk_data...
[nltk_data]   Package vader_lexicon is already up-to-date!


True

In [12]:
sia = SIA()
results = []

In [13]:
for line in reviews[:10]:
    pol_score = sia.polarity_scores(line)
    pol_score['headline'] = line
    results.append(pol_score)

pprint(results[1], width=100)

{'compound': -0.3374,
 'headline': "I really don't like the controls",
 'neg': 0.374,
 'neu': 0.626,
 'pos': 0.0}


In [14]:
pol_score = sia.polarity_scores(reviews[9999])
pol_score['headline'] = reviews[9999]
pol_score

{'neg': 0.227,
 'neu': 0.69,
 'pos': 0.082,
 'compound': -0.9718,
 'headline': 'I have already tried to refund this game, but I am past both dead lines, so it\'s kind of just sitting in my game library with no real purpose. I do not like how this game feel when you play it. The graphics, landscape, and driving might be fine, but the shooting, and chances of dying of some stupid cause makes me hate this game a lot more than I thought I would. I also do not enjoy that this out of many battle royale type survival series, have to have battle or "season pass". I have already spent money on your game, don\'t put options for better cosmetics and expect me to buy them.'}

In [15]:
sentiment_results = dict()

for review_id in range(len(reviews)):
    if review_id % 10000 == 0:
        print(review_id)
    sent_cat = list()
    review = reviews[review_id]
    position = position_list[review_id]
    review_window = review_windows[review_id]
    for sent_tuple in review_window:
        line = sent_tuple[0]
        category = sent_tuple[1]
        try:
            sent = sia.polarity_scores(line)
        except IndexError:
            print(IndexError)
            continue
        sent_cat.append((category, sent))
    sentiment_results[review_id] = sent_cat

0
10000
20000
30000
40000
50000
60000
70000
80000
90000
100000
110000
120000


In [16]:
sentiment_results

{0: [(2, {'neg': 0.438, 'neu': 0.562, 'pos': 0.0, 'compound': -0.5994})],
 1: [(0, {'neg': 0.322, 'neu': 0.678, 'pos': 0.0, 'compound': -0.3343})],
 2: [(6, {'neg': 0.269, 'neu': 0.479, 'pos': 0.251, 'compound': -0.0387}),
  (0, {'neg': 0.0, 'neu': 0.448, 'pos': 0.552, 'compound': 0.7506})],
 3: [(6, {'neg': 0.538, 'neu': 0.154, 'pos': 0.308, 'compound': -0.3612}),
  (6, {'neg': 0.0, 'neu': 0.075, 'pos': 0.925, 'compound': 0.9081}),
  (6, {'neg': 0.162, 'neu': 0.0, 'pos': 0.838, 'compound': 0.875}),
  (5, {'neg': 0.727, 'neu': 0.273, 'pos': 0.0, 'compound': -0.7906}),
  (5, {'neg': 0.569, 'neu': 0.431, 'pos': 0.0, 'compound': -0.765}),
  (5, {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}),
  (5, {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}),
  (3, {'neg': 0.0, 'neu': 0.794, 'pos': 0.206, 'compound': 0.0772}),
  (3, {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0})],
 4: [(1, {'neg': 0.0, 'neu': 0.246, 'pos': 0.754, 'compound': 0.8481})],
 5: [(1, {'neg': 0.0, 'neu'

In [ ]:
# ['gun', 'teamwork', 'loot', 'price', 'cheat', 'optimization', 'graphic']

## Feature Output -1

In [ ]:
cat_0_list = list()
cat_1_list = list()
cat_2_list = list()
cat_3_list = list()
cat_4_list = list()

for review_id in range(len(reviews)):
    cat_list = [0,0,0,0,0]
    n_list = [0,0,0,0,0]

    for sent in sentiment_results[review_id]:
        category = sent[0]
        score = sent[1]['compound']
        cat_list[category] += score
        n_list[category] += 1

    score_list = [0,0,0,0,0]
    for i in range(5):
        if n_list[i] != 0:
            score_list[i] = cat_list[i] / n_list[i]

    cat_0_list.append(score_list[0])
    cat_1_list.append(score_list[1])
    cat_2_list.append(score_list[2])
    cat_3_list.append(score_list[3])
    cat_4_list.append(score_list[4])

In [ ]:
all_list = [cat_0_list, cat_1_list, cat_2_list, cat_3_list, cat_4_list]

In [ ]:
from sklearn import preprocessing
minmax = preprocessing.MinMaxScaler()
cat_0_minmax = minmax.fit_transform(np.array(cat_0_list).reshape(-1,1)).flatten()
cat_1_minmax = minmax.fit_transform(np.array(cat_1_list).reshape(-1,1)).flatten()
cat_2_minmax = minmax.fit_transform(np.array(cat_2_list).reshape(-1,1)).flatten()
cat_3_minmax = minmax.fit_transform(np.array(cat_3_list).reshape(-1,1)).flatten()
cat_4_minmax = minmax.fit_transform(np.array(cat_4_list).reshape(-1,1)).flatten()

In [ ]:
# ['gameplay', 'price', 'cheat', 'optimization', 'graphic']
df_dict = {
    'review': reviews,
    'gameplay': cat_0_minmax,
    'price': cat_1_minmax,
    'cheat': cat_2_minmax,
    'optimization': cat_3_minmax,
    'graphic': cat_4_minmax,
}

df = pd.DataFrame(df_dict)

In [ ]:
df

In [ ]:
df.to_csv("2021_sentiment_feature.csv")

## Feature Output -2

In [17]:
len(sentiment_results)

125076

In [ ]:
# ['gun', 'teamwork', 'loot', 'price', 'cheat', 'optimization', 'graphic']

In [20]:
pos_cat_0_list = list()
pos_cat_1_list = list()
pos_cat_2_list = list()
pos_cat_3_list = list()
pos_cat_4_list = list()
pos_cat_5_list = list()
pos_cat_6_list = list()
neg_cat_0_list = list()
neg_cat_1_list = list()
neg_cat_2_list = list()
neg_cat_3_list = list()
neg_cat_4_list = list()
neg_cat_5_list = list()
neg_cat_6_list = list()

for review_id in range(len(reviews)):
#     cat_list = [(0,0),(0,0),(0,0),(0,0),(0,0)]
#     n_list = [(0,0),(0,0),(0,0),(0,0),(0,0)]
    cat_list = [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
    n_list = [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]

    for sent in sentiment_results[review_id]:
        
        category = sent[0]
#         print(category)
        positive_score = sent[1]['pos']
        negative_score = sent[1]['neg']
#         cat_list[category][0] += positive_score
#         cat_list[category][1] += negative_score
        cat_list[2*category] += positive_score
        cat_list[2*category+1] += negative_score
        
#         n_list[category][0] += 1
#         n_list[category][1] += 1
        n_list[2*category] += 1
        n_list[2*category+1] += 1 

#     score_list = [(0,0),(0,0),(0,0),(0,0),(0,0)]
    score_list = [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
    for i in range(5):
        if n_list[2*i] != 0:
            score_list[2*i] = cat_list[2*i] / n_list[2*i]
        if n_list[2*i+1] != 0:
            score_list[2*i+1] = cat_list[2*i+1] / n_list[2*i+1]

    pos_cat_0_list.append(score_list[0])
    neg_cat_0_list.append(score_list[1])
    pos_cat_1_list.append(score_list[2])
    neg_cat_1_list.append(score_list[3])
    pos_cat_2_list.append(score_list[4])
    neg_cat_2_list.append(score_list[5])
    pos_cat_3_list.append(score_list[6])
    neg_cat_3_list.append(score_list[7])
    pos_cat_4_list.append(score_list[8])
    neg_cat_4_list.append(score_list[9])
    pos_cat_5_list.append(score_list[10])
    neg_cat_5_list.append(score_list[11])
    pos_cat_6_list.append(score_list[12])
    neg_cat_6_list.append(score_list[13])

2
0
6
0
6
6
6
5
5
5
5
3
3
1
1
5
5
4
4
4
4
1
5
3
3
5
3
0
1
1
5
4
4
0
4
4
0
0
5
6
4
2
4
4
4
0
4
4
6
4
5
5
0
0
0
0
6
6
4
2
2
1
1
1
0
6
6
2
2
2
4
4
4
4
4
0
4
0
4
4
4
4
3
3
3
1
0
0
0
1
1
5
0
4
5
5
2
4
5
3
4
3
4
2
4
5
4
0
5
4
5
0
4
3
5
4
4
1
4
6
4
3
0
1
4
4
6
6
3
3
3
3
3
5
5
5
0
0
5
1
4
4
5
1
5
1
4
5
4
4
0
3
0
2
3
0
0
0
4
0
2
2
0
4
0
4
3
2
2
0
0
2
0
0
2
4
3
3
4
0
0
0
0
4
4
4
4
5
4
0
4
4
0
4
4
5
3
4
4
6
0
4
5
6
0
0
0
0
0
5
4
0
0
0
5
1
4
4
4
5
3
3
3
4
0
1
1
0
0
6
5
0
0
4
4
5
0
6
5
5
0
0
4
2
0
0
1
3
0
0
4
4
3
0
2
3
2
4
3
6
0
4
5
6
5
4
5
4
5
1
4
4
5
4
5
1
1
2
1
0
1
6
0
1
1
5
4
4
0
4
4
4
5
0
0
1
1
1
5
5
6
5
4
4
5
4
1
4
4
4
5
5
4
5
4
0
0
1
4
4
5
5
4
0
0
6
0
4
0
6
0
2
0
6
0
4
4
4
4
6
0
1
4
4
1
4
5
1
4
5
4
4
4
5
4
4
4
4
0
6
4
5
4
4
5
0
0
5
5
1
5
6
5
5
3
5
4
4
4
1
1
4
5
0
4
0
4
3
5
5
4
0
0
5
6
5
4
5
5
1
1
1
1
1
0
1
5
0
2
5
4
3
0
5
0
5
6
0
2
1
5
5
2
3
1
4
4
5
0
6
5
5
5
3
1
2
2
5
0
4
5
3
3
1
3
4
3
3
4
1
4
4
0
5
0
6
4
4
0
2
4
3
1
5
1
1
5
5
0
5
0
5
5
0
4
4
4
5
4
4
0
0
0
5
5
2
0
6
4
4
6
5
3
0
1
4
6
6
3
3


3
4
4
4
3
4
0
4
4
4
3
4
0
6
0
6
6
3
3
3
3
3
5
5
5
4
6
0
0
0
0
0
6
4
4
2
2
2
2
2
2
2
2
0
6
1
1
5
4
4
5
4
4
4
0
1
4
4
4
0
5
4
6
0
0
4
4
1
5
0
4
0
5
0
4
4
0
4
4
1
1
4
6
2
6
6
6
5
2
6
1
1
1
1
0
0
0
2
5
4
4
1
6
6
0
0
4
4
4
1
0
4
4
0
0
0
1
0
3
4
5
5
0
4
3
4
4
5
0
5
1
1
4
4
5
4
5
0
3
4
4
1
0
5
2
4
2
6
4
1
2
5
4
1
1
0
0
4
4
4
4
4
4
4
4
4
4
4
4
4
5
0
0
4
5
4
4
0
0
4
2
3
3
0
1
1
4
0
1
5
4
4
4
4
4
0
3
0
5
4
4
4
6
5
4
5
0
4
4
6
4
4
0
5
2
2
5
4
4
4
4
0
4
4
1
1
1
1
1
1
1
4
1
5
5
5
3
3
4
5
0
6
4
0
6
0
0
0
4
4
4
1
1
4
2
3
3
0
4
4
1
1
4
4
0
0
5
4
2
4
4
4
0
5
0
1
4
0
4
0
0
4
0
6
0
4
2
4
5
4
4
0
0
5
0
4
5
0
0
4
0
4
0
4
6
4
4
0
4
4
4
3
0
4
3
2
5
4
0
4
2
4
1
2
2
2
2
5
5
4
4
4
4
4
6
0
0
0
4
3
0
6
5
3
4
4
6
5
4
5
5
2
2
4
4
5
0
3
4
5
5
0
0
5
3
0
5
4
6
4
0
5
4
4
4
6
3
4
4
4
6
5
5
1
4
4
4
4
1
1
6
5
4
1
1
3
1
1
1
4
5
3
4
0
1
4
4
3
5
4
0
5
4
2
2
5
2
0
4
4
5
1
4
6
6
5
1
0
5
4
4
5
5
4
3
3
0
4
3
4
2
4
4
3
4
6
4
0
6
5
5
3
3
3
3
3
3
6
6
6
6
4
6
3
2
2
3
0
2
6
5
4
4
4
4
5
5
2
5
0
0
4
5
5
5
5
1
1
6
1
4
3
3
0
4
4
3
4
0
0


5
4
3
3
0
4
0
5
5
5
5
0
0
0
0
6
0
3
6
1
0
0
2
0
4
3
5
4
6
5
6
5
0
4
0
6
0
6
2
2
0
4
4
4
5
5
4
6
5
5
2
4
4
0
4
4
5
2
1
4
4
4
4
0
5
5
1
1
5
5
1
5
5
5
4
4
3
4
4
4
5
5
4
6
4
1
3
4
0
4
0
3
4
0
2
3
0
4
0
5
0
2
0
4
5
0
3
3
6
0
0
3
5
2
5
1
4
0
0
5
5
5
5
4
5
5
4
5
5
1
1
2
5
5
5
3
3
0
0
4
5
4
5
6
5
4
4
4
2
2
0
4
4
4
4
4
4
0
4
0
4
2
5
4
4
5
4
4
5
0
0
4
6
4
5
4
4
0
6
0
3
3
3
4
0
5
4
6
0
5
5
4
4
4
1
6
4
0
5
0
2
4
0
4
4
5
4
5
3
3
6
6
2
0
4
4
0
4
0
0
5
3
4
4
4
4
4
5
0
4
5
5
6
0
5
4
0
4
5
6
4
4
4
1
0
3
2
6
3
5
5
5
4
1
1
5
3
4
4
5
5
5
4
5
6
6
6
0
5
4
4
0
6
0
6
3
3
6
5
4
4
3
3
4
0
4
4
4
4
4
4
4
4
4
4
4
1
0
0
3
3
4
0
5
5
4
4
4
5
5
0
0
4
5
5
4
2
5
5
4
3
3
0
2
5
4
1
1
1
5
5
5
4
4
4
0
4
1
1
5
3
5
3
4
4
5
6
2
2
2
0
3
6
3
4
6
4
6
4
4
0
1
0
6
5
5
6
2
4
0
2
3
2
4
0
0
2
2
4
2
3
1
1
5
5
0
1
1
1
3
4
5
5
6
0
4
4
3
4
5
5
3
6
4
4
3
3
0
0
0
3
3
4
1
3
5
5
5
3
3
3
5
5
0
3
4
5
0
0
5
4
0
0
5
3
3
1
5
4
0
6
0
5
4
6
0
0
4
5
5
6
4
2
2
6
6
4
4
4
4
4
0
0
6
4
4
4
4
4
4
3
0
0
0
4
5
4
4
0
0
0
6
4
0
5
4
4
4
1
0
0
6
4
4
4
5
4
5
5
5


4
4
0
5
5
5
4
4
4
5
6
6
0
0
1
3
3
1
3
4
0
1
3
3
4
5
4
4
4
0
4
4
4
4
4
6
4
5
4
3
3
0
4
0
5
5
5
0
4
3
5
5
4
0
6
5
5
3
3
0
0
0
0
5
5
4
6
5
4
0
4
5
5
0
4
4
0
4
4
4
4
4
4
5
5
5
5
6
4
3
4
4
4
0
4
0
1
0
0
0
0
4
3
4
4
4
4
3
4
0
0
0
0
4
0
3
0
2
6
4
5
0
4
4
3
4
3
5
4
4
4
4
0
4
5
5
6
5
4
0
4
5
5
5
5
5
4
5
5
5
4
2
3
0
0
4
3
4
4
0
3
3
3
5
5
5
4
0
5
4
6
5
0
6
6
5
6
1
5
5
5
5
5
5
0
3
5
1
5
3
2
3
0
5
4
4
5
5
5
4
4
4
4
4
5
4
4
4
4
4
4
3
4
4
5
4
1
6
4
4
5
1
3
0
2
3
4
6
0
0
6
5
3
3
0
0
5
5
4
5
5
5
3
0
0
0
4
4
5
5
6
2
5
4
4
4
0
5
0
5
5
5
5
5
0
6
5
5
1
6
6
3
3
3
3
3
5
5
5
5
5
5
4
4
4
4
5
3
0
0
4
4
4
3
4
5
4
4
0
5
5
4
4
4
4
4
5
4
5
0
5
4
0
2
0
4
4
0
5
4
4
0
0
4
5
0
4
1
4
4
6
1
5
5
4
5
5
0
1
1
5
4
4
4
4
3
3
5
5
0
4
6
3
5
5
4
0
5
4
3
4
4
4
2
2
1
5
4
1
5
5
4
5
5
4
5
5
0
1
0
5
4
5
5
0
5
4
5
0
5
4
1
5
4
5
4
4
5
5
4
0
4
2
6
3
4
3
3
6
1
5
4
4
3
0
4
4
4
4
4
4
4
4
1
4
4
4
3
4
5
1
0
4
5
4
4
5
2
4
4
0
4
0
5
5
5
6
5
5
4
4
1
4
5
4
5
5
4
0
4
4
4
4
5
5
4
6
0
4
4
4
0
4
5
4
6
5
1
1
4
4
4
4
4
4
6
1
4
4
3
4
1
3
0
1
4
0
6
6
2


0
1
4
3
0
4
4
4
5
6
0
0
4
0
0
0
0
0
0
1
5
6
1
3
5
0
6
0
6
0
0
5
4
5
2
5
4
3
2
6
2
0
3
0
1
1
3
5
2
4
5
4
3
3
6
4
6
4
4
4
4
4
4
0
4
5
5
4
5
5
5
0
1
5
5
1
0
5
4
4
0
5
4
3
5
5
5
5
4
4
4
4
4
4
0
4
5
2
3
2
5
4
0
0
3
3
1
0
4
5
5
0
5
1
0
1
1
4
4
4
1
5
5
0
5
4
1
5
3
3
1
1
1
0
0
5
0
4
1
1
6
5
0
4
4
4
0
0
4
0
4
5
4
4
3
6
0
3
5
5
4
6
0
6
4
5
5
5
5
0
2
2
1
5
3
5
5
5
5
5
5
0
5
5
5
0
4
6
4
5
4
3
6
5
5
0
5
4
5
4
5
5
5
4
4
4
0
5
4
2
0
4
4
5
4
3
5
5
4
5
5
5
3
1
1
0
1
0
5
4
5
4
2
5
0
1
4
4
1
1
4
4
4
4
5
4
3
3
5
0
4
4
4
4
4
4
5
4
4
3
4
5
4
0
4
5
2
4
3
4
1
6
5
5
5
5
5
4
5
5
4
4
4
0
0
4
4
4
4
4
4
3
0
6
4
4
4
3
4
1
4
1
1
5
0
0
3
0
0
4
0
5
3
0
0
5
5
5
5
5
4
2
2
3
4
5
5
4
4
4
5
5
0
4
3
3
4
3
3
4
4
1
1
6
0
4
5
0
0
1
1
3
2
4
1
4
2
5
5
5
5
5
3
5
2
1
6
5
4
5
0
5
3
3
4
1
5
5
5
6
5
5
5
1
5
5
2
4
0
0
0
0
5
5
0
4
4
0
3
5
1
5
1
5
4
1
5
4
5
0
1
0
0
6
4
4
4
3
1
4
4
4
3
2
4
2
5
2
2
1
4
0
4
0
5
2
4
4
4
0
5
1
3
4
4
5
4
4
1
4
4
4
4
1
4
5
5
5
4
6
4
0
0
0
0
0
0
0
0
5
3
4
6
4
5
3
4
4
0
4
4
2
4
5
5
4
4
5
4
5
1
1
5
0
4
4
2
2
2
0


...

0
1
1
4
5
0
0
1
3
3
5
3
2
0
2
2
1
2
2
4
3
4
4
4
5
6
5
4
6
3
3
1
6
5
5
0
5
0
0
0
0
0
0
3
0
4
6
0
3
0
5
0
3
4
1
5
4
5
5
0
0
2
0
0
5
0
4
2
2
5
1
0
4
5
5
4
5
5
4
5
0
3
3
4
2
2
5
5
0
5
3
0
0
5
6
0
0
0
0
0
0
0
0
0
0
0
2
2
2
6
2
2
6
0
0
0
2
2
5
5
5
5
0
4
5
5
4
0
4
4
5
0
0
2
5
0
3
5
4
5
4
5
5
2
5
5
5
3
4
4
1
1
0
1
1
5
4
3
0
5
1
5
2
5
5
1
0
2
2
2
1
3
1
1
0
5
4
1
1
3
0
6
2
2
0
2
0
0
2
1
5
4
2
5
0
5
5
5
5
5
5
0
5
5
4
0
4
4
4
3
0
2
0
5
4
2
6
0
2
2
0
1
2
3
6
5
5
6
2
3
5
5
5
5
5
5
1
3
3
5
5
5
5
3
3
4
5
5
4
5
0
5
4
5
4
0
6
5
6
5
0
6
0
6
6
4
4
4
5
5
5
0
4
5
4
5
5
0
4
0
0
3
5
3
3
0
5
4
4
4
4
5
0
0
6
4
5
5
6
4
0
2
1
0
0
1
4
0
3
5
5
5
5
3
1
4
0
0
0
2
6
5
5
3
3
5
6
6
3
3
5
5
2
2
2
2
2
2
2
0
3
2
0
4
0
2
0
0
2
0
2
4
2
3
2
0
5
0
0
5
5
5
5
5
4
3
3
5
5
6
4
4
2
5
0
5
5
5
2
0
6
5
1
5
5
4
5
1
1
1
5
5
3
5
5
6
0
5
6
1
1
2
5
5
5
5
3
6
0
6
4
4
0
0
6
5
1
1
1
0
2
5
5
6
2
2
2
2
4
2
2
2
5
0
4
3
1
5
5
5
4
5
0
5
4
0
5
4
4
1
5
5
4
5
6
5
5
5
4
0
0
5
0
5
1
0
5
0
0
4
0
5
6
0
0
2
3
0
3
4
4
4
5
4
4
5
0
1
1
4
0
5
0
5
1
2
0
5
1
0


0
6
0
2
3
4
4
0
5
0
4
5
0
0
5
5
5
5
4
4
4
5
5
5
0
5
5
5
5
5
5
6
0
5
5
3
5
4
5
0
0
6
5
5
2
0
5
4
4
0
0
0
5
6
5
5
5
5
6
6
5
1
5
5
1
6
1
2
1
3
3
1
2
2
0
0
4
3
0
0
5
6
3
3
1
1
5
1
5
4
4
5
5
5
4
5
2
6
0
0
6
2
2
2
2
5
6
5
6
5
2
2
2
2
4
3
0
5
0
0
0
2
1
1
5
4
5
5
3
0
5
0
5
5
0
0
0
5
2
0
5
5
5
0
2
0
0
2
2
0
0
1
2
0
4
5
5
0
4
2
0
2
2
1
0
3
1
5
0
5
4
4
5
4
4
4
5
5
0
5
5
0
0
6
3
1
0
0
1
5
5
5
5
4
1
0
0
0
5
5
4
5
1
5
5
6
3
0
3
4
1
0
2
0
0
5
0
2
0
2
6
0
2
0
2
0
0
5
6
2
2
2
2
5
5
1
1
1
0
0
2
0
5
5
5
3
3
5
5
0
5
5
0
5
4
1
0
5
4
5
0
5
4
1
1
5
4
0
3
5
3
5
3
3
5
5
5
4
0
5
4
0
5
5
5
3
1
1
2
0
3
3
0
0
0
5
0
5
0
0
1
2
0
0
0
2
1
1
0
5
5
5
5
5
5
3
4
4
0
6
0
0
5
5
5
4
0
0
0
1
1
0
0
0
0
2
2
0
2
6
3
3
5
5
3
4
0
5
0
0
1
0
0
5
0
5
6
3
6
6
3
0
5
4
5
4
5
1
5
0
5
5
5
0
4
0
0
0
5
4
4
0
0
3
2
5
4
4
4
4
1
0
4
5
4
4
5
1
0
5
5
5
2
5
5
5
4
5
5
4
0
0
5
6
5
5
1
5
4
4
3
0
3
0
2
3
4
4
5
5
0
2
0
4
1
5
1
4
2
5
5
5
4
4
4
2
3
5
2
5
5
0
1
0
0
0
0
4
5
2
2
0
5
4
0
4
0
4
2
5
2
5
0
0
0
0
0
0
0
0
6
0
0
0
2
2
2
2
2
5
5
4
5
5
5
5
5
0
4
3


3
6
0
0
5
4
5
0
4
4
0
4
4
5
4
5
3
0
4
0
0
5
5
5
5
5
5
4
0
3
0
0
2
0
2
5
5
5
5
5
5
4
0
0
0
0
5
4
0
0
1
0
0
3
0
0
0
3
0
4
4
5
6
4
4
4
5
0
4
4
0
4
1
5
2
5
3
5
5
5
4
3
3
3
1
5
5
0
5
5
0
1
5
0
5
6
0
6
1
1
0
6
0
6
2
2
2
3
3
5
1
5
5
2
6
0
0
5
5
5
5
6
4
0
2
0
4
5
4
6
5
5
5
5
5
1
1
5
0
3
3
5
0
5
5
0
5
5
0
5
0
6
5
3
5
2
2
6
2
4
2
2
2
0
0
6
5
6
6
0
5
4
5
4
5
0
0
3
5
5
4
1
4
4
4
4
2
0
0
0
4
4
4
0
5
6
5
0
1
1
1
4
0
2
0
5
2
1
5
5
3
5
0
5
5
5
2
0
0
5
6
4
1
4
3
5
0
4
5
6
0
5
0
4
0
5
4
5
0
3
5
0
4
1
1
5
0
5
5
2
5
0
5
5
0
5
0
5
5
0
5
0
5
5
5
5
0
0
5
5
5
0
1
5
5
5
4
6
0
5
0
5
5
4
0
0
3
5
4
3
5
5
0
2
5
5
5
5
0
4
3
4
5
4
4
4
4
6
6
0
0
0
5
4
0
6
2
2
2
5
5
4
6
0
3
5
5
0
5
5
5
5
5
3
5
4
4
5
4
6
2
5
0
5
5
0
3
3
5
5
0
5
4
4
5
1
1
1
1
3
5
5
0
2
0
5
5
4
6
2
0
3
3
0
3
4
3
6
2
0
2
0
2
0
2
2
2
2
2
1
6
3
5
3
3
1
3
5
1
5
5
5
6
2
5
2
5
4
5
5
0
3
3
5
5
5
5
0
2
5
5
0
5
4
4
4
5
3
5
5
6
6
5
1
0
4
5
4
2
2
3
6
3
5
5
1
5
5
6
5
4
3
4
5
3
0
5
5
4
1
4
5
4
5
4
6
1
3
3
0
5
5
4
5
5
0
5
5
3
4
4
2
4
0
5
0
4
0
2
5
4
0
5
3
5
0
0
3
5
3


4
0
4
6
4
4
0
3
5
0
5
0
5
4
3
3
0
5
6
5
0
3
1
1
1
1
0
1
1
1
1
1
1
5
5
1
1
4
5
5
5
5
5
5
5
5
0
1
5
4
5
5
5
5
5
5
5
3
5
4
0
0
6
3
0
1
5
5
5
0
0
0
5
5
0
2
2
4
3
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
3
0
5
5
0
4
3
5
5
1
0
5
5
4
5
3
5
5
5
0
2
0
0
0
1
1
5
0
5
5
5
5
0
1
4
1
3
0
2
2
2
2
4
3
2
4
4
0
4
4
5
3
4
5
5
1
1
6
0
5
4
4
5
5
1
1
0
2
0
5
5
5
0
2
5
1
1
0
0
1
1
1
6
6
1
1
4
5
0
5
2
6
2
0
2
6
5
6
5
5
5
0
5
5
6
2
5
1
5
1
5
5
5
5
0
5
4
4
5
0
3
3
5
3
3
0
0
2
0
4
0
4
5
5
5
0
0
5
5
0
5
5
4
4
5
0
0
2
5
5
0
0
5
6
5
0
0
4
2
6
3
5
3
2
0
5
5
5
5
5
5
5
0
2
2
2
1
1
1
0
1
2
2
2
5
5
5
4
5
3
6
0
6
1
5
4
4
5
4
5
4
5
0
0
6
5
4
3
0
3
3
3
5
0
4
4
5
4
0
0
5
4
5
6
4
5
4
5
5
5
4
6
4
0
0
0
0
0


4
1
1
4
2
5
5
5
5
5
5
3
3
4
5
5
5
5
4
4
5
4
4
4
5
5
4
5
4
5
4
0
4
2
4
4
4
4
4
4
5
4
5
5
0
5
6
5
0
0
1
1
0
2
1
5
6
5
5
0
6
0
0
0
5
5
0
0
2
5
4
4
4
4
5
5
4
6
6
4
5
2
5
4
1
4
5
5
2
5
5
0
0
0
0
0
5
6
1
1
5
3
0
4
0
5
5
2
5
2
5
5
0
4
1
0
0
3
4
5
5
5
5
0
0
0
0
1
1
1
5
4
5
5
4
5
5
0
4
2
5
2
2
0
5
1
5
5
5
5
4
5
3
5
2
5
5
5
5
5
0
4
0
0
5
5
3
0
0
5
3
3
0
0
1
5
0
6
5
0
4
5
4
6
6
0
2
2
4
4
4
5
0
4
5
4
5
4
4
5
5
5
3
0
0
5
0
4
5
5
3
6
6
2
6
2
6
2
2
0
4
5
0
5
4
5
5
5
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
0
0
0
0
0
0
6
5
4
5
0
1
1
0
5
0
0
5
3
3
0
0
2
2
5
4
4
5
4
0
4
1
0
5
5
5
2
5
5
4
6
0
1
1
0
3
6
5
5
5
4
4
1
4
5
5
5
0
5
0
0
2
0
0
3
5
5
5
5
1
2
4
5
5
4
0
4
5
4
0
4
4
5
1
5
5
0
5
4
0
5
2
2
5
0
4
4
4
4
5
5
4
5
3
4
4
4
5
0
2
5
5
6
0
2
5
4
4
5
5
2
3
3
3
6
5
6
0
0
0
5
4
5
5
1
1
5
5
1
5
5
4
0
0
5
5
4
5
3
6
0
6
3
3
1
4
0
4
5
5
4
4
4
1
4
4
4
5
2
0
5
1
5
3
6
3
3
0
0
0
0
2
2
0
0
0
0
3
2
4
0
5
5
5
5
3
5
0
5
5
4
3
5
0
1
1
1
1
0
0
0
0
0
0
0
0
0
0
5
5
6
2
5
5
6
5
3
0
5
5
5
3
4
0
0
4
0
0
2
2
4
2
0
4
1
4
2
0
4
0
4
5
0
5
4
4


In [ ]:
# ['gun', 'teamwork', 'loot', 'price', 'cheat', 'optimization', 'graphic']

In [ ]:
df_dict = {
    'review': reviews,
    'gun_pos': pos_cat_0_list,
    'gun_neg': neg_cat_0_list,
    'teamwork_pos': pos_cat_1_list,
    'teamwork_neg': neg_cat_1_list,
    'loot_pos': pos_cat_2_list,
    'loot_neg': neg_cat_2_list,
    'price_pos': pos_cat_3_list,
    'price_neg': neg_cat_3_list,
    'cheat_pos': pos_cat_4_list,
    'cheat_neg': neg_cat_4_list,
    'optimization_pos': pos_cat_5_list,
    'optimization_neg': neg_cat_5_list,
    'graphic_pos': pos_cat_6_list,
    'graphic_neg': neg_cat_6_list
}

df = pd.DataFrame(df_dict)

In [22]:
def positive_filter(x):
    if x >= 0.2:
        return 1
    else:
        return 0
    
def negative_filter(x):
    if x >= 0.2:
        return 1
    else:
        return 0

In [23]:
df_dict = {
    'review': reviews,
    'gameplay_pos': list(map(positive_filter, pos_cat_0_list)),
    'gameplay_neg': list(map(negative_filter, neg_cat_0_list)),
    'price_pos': list(map(positive_filter, pos_cat_1_list)),
    'price_neg': list(map(negative_filter, neg_cat_1_list)),
    'cheat_pos': list(map(positive_filter, pos_cat_2_list)),
    'cheat_neg': list(map(negative_filter, neg_cat_2_list)),
    'optimization_pos': list(map(positive_filter, pos_cat_3_list)),
    'optimization_neg': list(map(negative_filter, neg_cat_3_list)),
    'graphic_pos': list(map(positive_filter, pos_cat_4_list)),
    'graphic_neg': list(map(negative_filter, neg_cat_4_list))
}

df = pd.DataFrame(df_dict)

In [24]:
df

review  gameplay_pos  \
0                CHUTE LOOT DIE THATS PUBG IN A NUT SHELL             0   
1                        I really don't like the controls             0   
2       Graphics are pretty bad but the gameplay is ok...             1   
3       ☼ Graphics ☼\r\r\n☐ Bad\r\r\n☐ Alright\r\r\n☐ ...             0   
4                     Excellent game to play with friends             0   
...                                                   ...           ...   
125071  I only played maybe an hour of this game, then...             0   
125072  Personally I think its better than warzone jus...             0   
125073  Honestly this was the best battle royal ever, ...             1   
125074               games full of hackers and exploiters             0   
125075     game is buggy as hell and crashes all the time             0   

        gameplay_neg  price_pos  price_neg  cheat_pos  cheat_neg  \
0                  0          0          0          0          1   
1                  1          0          0          0          0   
2                  0          0          0          0          0   
3                  0          0          0          0          0   
4                  0          1          0          0          0   
...              ...        ...        ...        ...        ...   
125071             0          0          0          0          0   
125072             0          0          0          0          0   
125073             0          0          0          0          0   
125074             0          0          0          0          0   
125075             0          0          0          0          0   

        optimization_pos  optimization_neg  graphic_pos  graphic_neg  
0                      0                 0            0            0  
1                      0                 0            0            0  
2                      0                 0            0            0  
3                      0                 0            0            0  
4                      0                 0            0            0  
...                  ...               ...          ...          ...  
125071                 0                 0            0            1  
125072                 0                 0            0            0  
125073                 0                 0            0            0  
125074                 0                 0            0            0  
125075                 0                 0            0            0  

[125076 rows x 11 columns]

In [25]:
df.to_csv("20220108_sentiment_feature.csv")